In [1]:
import sys
sys.path.insert(0, '../')
import gc
import logging
logging.basicConfig(level=logging.DEBUG)

from cryptotrader.envs.driver import Apocalipse, get_historical
from cryptotrader.agents import apriori
from cryptotrader.random_process import ConstrainedOrnsteinUhlenbeckProcess
from cryptotrader.envs.utils import make_env, get_dfs_from_db
from cryptotrader.utils import convert_to, array_normalize

import pandas as pd
import pymongo as pm
from bokeh.io import output_notebook
from jupyterthemes import jtplot
output_notebook()
jtplot.style()
%matplotlib inline
import os
import numpy as np
np.random.seed(42)

# %load_ext line_profiler

Loading BokehJS ...

In [2]:
seed = 42
outdir = './logs'
# data_dir = '../historical_data/'
# files = []
# for file in os.listdir(data_dir):
#     files.append(data_dir + file)

# Env params
freq = 30
obs_steps = 300
tax = 0.0025
init_fiat = 100.0
init_crypto = 0.0
max_eval_steps = 500
eval_runs = 1500
test = True

In [3]:
# env = make_env(True, 10, obs_steps=obs_steps, freq=freq, tax=tax, init_fiat=init_fiat, init_crypto=init_crypto, seed=seed)
# env = make_env(True, len(files), obs_steps, freq=freq, tax=tax, init_fiat=init_fiat, init_crypto=init_crypto, toy=False, files=files)

In [4]:
# client = pm.MongoClient(host='192.168.1.100', port=27017, connect=True)
# db = client.db

# env = Apocalipse(name='poloniex_momentum_outofsample', seed=seed)
# # Set environment options
# env.set_freq(freq)
# env.set_obs_steps(obs_steps)

# symbols, dfs = get_dfs_from_db(db, 'poloniex', start='2017-02-00 00:00:00', end='2017-05-00 00:00:00', freq=str(freq) + 'min')
    
def convert_and_clean(x):
    x = x.apply(convert_to.decimal)
    f = x.rolling(30, center=True, min_periods=1).mean().apply(convert_to.decimal)
    x = x.apply(lambda x: x if x.is_finite() else np.nan)
    return x.combine_first(f)    

# # Add backtest data
# for i, symbol in enumerate(symbols):
#     for col in dfs[i].columns:
#         dfs[i][col] = convert_and_clean(dfs[i][col])
#     env.add_df(df=dfs[i], symbol=symbol)
#     env.add_symbol(symbol)
#     env.set_init_crypto(init_crypto, symbol)
#     env.set_tax(tax, symbol)
# # del dfs, symbols

# gc.collect()
# env.set_init_fiat(init_fiat)

# # Clean pools
# env._reset_status()
# env.clear_dfs()
# gc.collect()

# env.set_training_stage(False)
# env.set_observation_space()
# env.set_action_space()
# env.reset(reset_funds=True, reset_results=True, reset_global_step=True);

In [5]:
# client = pm.MongoClient(host='192.168.1.100', port=27017, connect=True)
# db = client.db

env = Apocalipse(name='poloniex_momentum_backtest', seed=seed)
# Set environment options
env.set_freq(freq)
env.set_obs_steps(obs_steps)

symbols = ['usdtbtc', 'usdteth', 'usdtetc', 'usdtxrp', 'usdtltc']
for i, symbol in enumerate(symbols):
    df = pd.read_csv('./'+symbol+'_fev_may.csv')
    df['date'] = df.date.apply(pd.to_datetime)
    df = df.set_index('date')
    for col in df.columns:
        df[col] = convert_and_clean(df[col])
    env.add_df(df=df, symbol=symbol)
    env.add_symbol(symbol)
    env.set_init_crypto(init_crypto, symbol)
    env.set_tax(tax, symbol)

gc.collect()
env.set_init_fiat(init_fiat)

# Clean pools
env._reset_status()
env.clear_dfs()
gc.collect()

env.set_training_stage(False)
env.set_observation_space()
env.set_action_space()
env.reset(reset_funds=True, reset_results=True, reset_global_step=True);

INFO:Cryptocoin arbiter agent logging file:[poloniex_momentum_backtest Apocalipse initialization]
Apocalipse Initialized!
ONLINE MODE: False


INFO:Cryptocoin arbiter agent logging file:[<function Apocalipse.set_action_space at 0x7fe715342d08>]
Setting environment with 6 symbols.



In [6]:
random_process = ConstrainedOrnsteinUhlenbeckProcess(theta=1.0, size=env.action_space.low.shape[0])
random_agent = apriori.DummyTrader(random_process=random_process)

env.reset(reset_funds=True, reset_results=True, reset_global_step=True)
random_agent.test(env, nb_episodes=1, action_repetition=1, callbacks=None,
            visualize=False, nb_max_episode_steps=None, nb_max_start_steps=0, start_step_policy=None, verbose=True)

env.plot_results(env._get_results());

################### > Portifolio Performance Analysis < ###################-1 days +23:59:58.494569    

Portifolio excess Sharpe:                 -0.037336
Portifolio / Benchmark Sharpe ratio:      0.742993 / 0.729218
Portifolio / Benchmark Omega ratio:       1.177542 / 1.232880
Portifolio / Benchmark max drawdown:      -1.292271 / -82209.307292


In [7]:
ed_agent = apriori.EqualyDistributedTrader()
env.set_training_stage(False)
env.reset(reset_funds=True, reset_results=True, reset_global_step=True)
ed_agent.test(env, verbose=True)

env.plot_results(env._get_results());

################### > Portifolio Performance Analysis < ###################-1 days +23:59:58.494569   

Portifolio excess Sharpe:                 0.001077
Portifolio / Benchmark Sharpe ratio:      1.269010 / 0.729218
Portifolio / Benchmark Omega ratio:       1.316022 / 1.232880
Portifolio / Benchmark max drawdown:      -126.127423 / -82209.307292


In [8]:
# Optimize model hiperparameters
momentum_agent = apriori.MomentumTrader()

# env.set_training_stage(True)
# env.reset(reset_funds=True, reset_results=True, reset_global_step=True)

# opt_params, info = momentum_agent.fit(env, eval_runs, action_repetition=1, callbacks=None, verbose=True,
#             visualize=False, nb_max_start_steps=0, start_step_policy=None, log_interval=10000,
#             nb_max_episode_steps=max_eval_steps)

# print("\nOptimum parameters:", opt_params)

env.set_training_stage(False)
env.reset(reset_funds=True, reset_global_step=True, reset_results=True)
momentum_agent.set_params(**{'ma1': 39, 'ma2': 270, 'std_span': 299, 'std_weight_down': 1.9648256750026283, 'std_weight_up': 2.1424218749999993})
momentum_agent.test(env, nb_episodes=1, action_repetition=1, callbacks=None,
            visualize=False, nb_max_episode_steps=None, nb_max_start_steps=0, start_step_policy=None, verbose=True)

print("\nEnv params: \nInit fiat: {}\nInit crypto: {}\nFreq: {}".format(env.init_fiat, env.init_crypto, env.freq))
env.plot_results(env._get_results());

>> step 3972/3972, 100 % done, Cumulative Reward: 1.530220693347328, ETC: -1 days +23:59:58.494569   
Env params: 
Init fiat: 100.00000000
Init crypto: {'usdtbtc': Decimal('0E-8'), 'usdteth': Decimal('0E-8'), 'usdtetc': Decimal('0E-8'), 'usdtxrp': Decimal('0E-8'), 'usdtltc': Decimal('0E-8')}
Freq: 30
################### > Portifolio Performance Analysis < ###################

Portifolio excess Sharpe:                 -0.014695
Portifolio / Benchmark Sharpe ratio:      0.518045 / 0.729218
Portifolio / Benchmark Omega ratio:       1.143634 / 1.232880
Portifolio / Benchmark max drawdown:      -123437.437799 / -82209.307292


In [9]:
# # Optimize model hiperparameters
mesa_agent = apriori.MesaMomentumTrader()

env.set_training_stage(True)
env.reset(reset_funds=True, reset_results=True, reset_global_step=True)

opt_params, info = mesa_agent.fit(env, eval_runs, action_repetition=1, callbacks=None, verbose=True,
            visualize=False, nb_max_start_steps=0, start_step_policy=None, log_interval=10000,
            nb_max_episode_steps=max_eval_steps)

print("\nOptimum parameters:", opt_params)
env.set_training_stage(False)
env.reset(reset_funds=True, reset_global_step=True, reset_results=True)

mesa_agent.test(env, nb_episodes=1, action_repetition=1, callbacks=None,
            visualize=False, nb_max_episode_steps=None, nb_max_start_steps=0, start_step_policy=None, verbose=True)

print("\nEnv params: \nInit fiat: {}\nInit crypto: {}\nFreq: {}".format(env.init_fiat, env.init_crypto, env.freq))
env.plot_results(env._get_results());

Optimization step 1469/1500, step reward: 0.2993513783818571, ETC: 0 days 00:00:46.700493 4  7 
Optimum parameters: {'ma1': 0.16750944148524377, 'ma2': 0.1055320822065476}
>> step 3972/3972, 100 % done, Cumulative Reward: 0.6683157616727221, ETC: -1 days +23:59:58.494544    
Env params: 
Init fiat: 100.00000000
Init crypto: {'usdtbtc': Decimal('0E-8'), 'usdteth': Decimal('0E-8'), 'usdtetc': Decimal('0E-8'), 'usdtxrp': Decimal('0E-8'), 'usdtltc': Decimal('0E-8')}
Freq: 30
################### > Portifolio Performance Analysis < ###################

Portifolio excess Sharpe:                 -0.037735
Portifolio / Benchmark Sharpe ratio:      0.313292 / 0.729218
Portifolio / Benchmark Omega ratio:       1.091344 / 1.232880
Portifolio / Benchmark max drawdown:      -1.775228 / -82209.307292


In [10]:
env = Apocalipse(name='poloniex_momentum_oos', seed=seed)
# Set environment options
env.set_freq(freq)
env.set_obs_steps(obs_steps)

symbols = ['usdtbtc', 'usdteth', 'usdtetc', 'usdtxrp', 'usdtltc']
for i, symbol in enumerate(symbols):
    df = pd.read_csv('./'+symbol+'_may.csv')
    df['date'] = df.date.apply(pd.to_datetime)
    df = df.set_index('date')
    for col in df.columns:
        df[col] = convert_and_clean(df[col])
    env.add_df(df=df, symbol=symbol)
    env.add_symbol(symbol)
    env.set_init_crypto(init_crypto, symbol)
    env.set_tax(tax, symbol)

gc.collect()
env.set_init_fiat(init_fiat)

# Clean pools
env._reset_status()
env.clear_dfs()
gc.collect()

env.set_training_stage(False)
env.set_observation_space()
env.set_action_space()
env.reset(reset_funds=True, reset_results=True, reset_global_step=True);

INFO:Cryptocoin arbiter agent logging file:[poloniex_momentum_oos Apocalipse initialization]
Apocalipse Initialized!
ONLINE MODE: False


INFO:Cryptocoin arbiter agent logging file:[<function Apocalipse.set_action_space at 0x7fe715342d08>]
Setting environment with 6 symbols.



In [11]:
momentum_agent.test(env, nb_episodes=1, action_repetition=1, callbacks=None,
            visualize=False, nb_max_episode_steps=None, nb_max_start_steps=0, start_step_policy=None, verbose=True)

print("\nEnv params: \nInit fiat: {}\nInit crypto: {}\nFreq: {}".format(env.init_fiat, env.init_crypto, env.freq))
env.plot_results(env._get_results());

>> step 6109/6109, 100 % done, Cumulative Reward: 1.490223778453132, ETC: -1 days +23:59:58.494544   
Env params: 
Init fiat: 100.00000000
Init crypto: {'usdtbtc': Decimal('0E-8'), 'usdteth': Decimal('0E-8'), 'usdtetc': Decimal('0E-8'), 'usdtxrp': Decimal('0E-8'), 'usdtltc': Decimal('0E-8')}
Freq: 30
################### > Portifolio Performance Analysis < ###################

Portifolio excess Sharpe:                 0.003696
Portifolio / Benchmark Sharpe ratio:      0.173839 / 0.164676
Portifolio / Benchmark Omega ratio:       1.041639 / 1.033025
Portifolio / Benchmark max drawdown:      -inf / -inf


/home/casa/virtualenvs/tau/lib/python3.6/site-packages/empyrical/stats.py:135: RuntimeWarning: overflow encountered in multiply
  return df_cum * starting_value
/home/casa/virtualenvs/tau/lib/python3.6/site-packages/empyrical/stats.py:232: RuntimeWarning: invalid value encountered in subtract
  return nanmin((cumulative - max_return) / max_return)
/home/casa/virtualenvs/tau/lib/python3.6/site-packages/empyrical/stats.py:232: RuntimeWarning: invalid value encountered in true_divide
  return nanmin((cumulative - max_return) / max_return)
/home/casa/virtualenvs/tau/lib/python3.6/site-packages/empyrical/stats.py:232: RuntimeWarning: overflow encountered in subtract
  return nanmin((cumulative - max_return) / max_return)


In [13]:
# mesa_agent.test(env, nb_episodes=1, action_repetition=1, callbacks=None,
#             visualize=False, nb_max_episode_steps=None, nb_max_start_steps=0, start_step_policy=None, verbose=True)

print("\nEnv params: \nInit fiat: {}\nInit crypto: {}\nFreq: {}".format(env.init_fiat, env.init_crypto, env.freq))
env.plot_results(env._get_results());


Env params: 
Init fiat: 100.00000000
Init crypto: {'usdtbtc': Decimal('0E-8'), 'usdteth': Decimal('0E-8'), 'usdtetc': Decimal('0E-8'), 'usdtxrp': Decimal('0E-8'), 'usdtltc': Decimal('0E-8')}
Freq: 30
################### > Portifolio Performance Analysis < ###################

Portifolio excess Sharpe:                 -0.002964
Portifolio / Benchmark Sharpe ratio:      0.208719 / 0.164676
Portifolio / Benchmark Omega ratio:       1.049823 / 1.033025
Portifolio / Benchmark max drawdown:      -16.750806 / -inf


/home/casa/virtualenvs/tau/lib/python3.6/site-packages/empyrical/stats.py:135: RuntimeWarning: overflow encountered in multiply
  return df_cum * starting_value
/home/casa/virtualenvs/tau/lib/python3.6/site-packages/empyrical/stats.py:232: RuntimeWarning: overflow encountered in subtract
  return nanmin((cumulative - max_return) / max_return)
/home/casa/virtualenvs/tau/lib/python3.6/site-packages/empyrical/stats.py:232: RuntimeWarning: invalid value encountered in subtract
  return nanmin((cumulative - max_return) / max_return)
/home/casa/virtualenvs/tau/lib/python3.6/site-packages/empyrical/stats.py:232: RuntimeWarning: invalid value encountered in true_divide
  return nanmin((cumulative - max_return) / max_return)
